# Forewords

1. This notebook covers the data preprocessing step of the preprocessing process for the project. Please follow the steps outlined in the dataset folder to download the dataset before attempting this notebook.
2. If you followed the previous steps, you would have had the csv file and audio files saved on your Google Drive and ready for use.
3. Please update the directory path below to your Google Drive path for the respective files as needed.

<a href="https://colab.research.google.com/github/rachlllg/Project_Bird-Song-Classifier-with-Machine-Learning/blob/main/preprocessing.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Import Libraries

In [1]:
# drive access
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [2]:
# standard libraries
import numpy as np
import pandas as pd

In [3]:
# for audio
from IPython.display import Audio
import librosa

In [4]:
# for train_test split
from sklearn.model_selection import train_test_split

# Load train_metadata.csv

In [5]:
# change the file path to your local path
df = pd.read_csv('/content/drive/MyDrive/project/train_metadata.csv')

df.head()

primary_label secondary_labels              type  latitude  longitude  \
0       abethr1               []          ['song']    4.3906    38.2788   
1       abethr1               []          ['call']   -2.9524    38.2921   
2       abethr1               []          ['song']   -2.9524    38.2921   
3       abethr1               []          ['song']   -2.9524    38.2921   
4       abethr1               []  ['call', 'song']   -2.9524    38.2921   

      scientific_name               common_name         author  \
0  Turdus tephronotus  African Bare-eyed Thrush  Rolf A. de By   
1  Turdus tephronotus  African Bare-eyed Thrush  James Bradley   
2  Turdus tephronotus  African Bare-eyed Thrush  James Bradley   
3  Turdus tephronotus  African Bare-eyed Thrush  James Bradley   
4  Turdus tephronotus  African Bare-eyed Thrush  James Bradley   

                                             license  rating  \
0  Creative Commons Attribution-NonCommercial-Sha...     4.0   
1  Creative Commons Attribution-NonCommercial-Sha...     3.5   
2  Creative Commons Attribution-NonCommercial-Sha...     3.5   
3  Creative Commons Attribution-NonCommercial-Sha...     5.0   
4  Creative Commons Attribution-NonCommercial-Sha...     4.5   

                                 url              filename  
0  https://www.xeno-canto.org/128013  abethr1/XC128013.ogg  
1  https://www.xeno-canto.org/363501  abethr1/XC363501.ogg  
2  https://www.xeno-canto.org/363502  abethr1/XC363502.ogg  
3  https://www.xeno-canto.org/363503  abethr1/XC363503.ogg  
4  https://www.xeno-canto.org/363504  abethr1/XC363504.ogg

In [6]:
df['primary_label'].value_counts()

barswa     500
wlwwar     500
thrnig1    500
eaywag1    500
comsan     500
          ... 
lotcor1      1
whctur2      1
whhsaw1      1
afpkin1      1
crefra2      1
Name: primary_label, Length: 264, dtype: int64

# Preprocessing

## 1. include only the 3 species selected (barswa, comsan, and eaywag1)

In [7]:
interested_species = ['barswa', 'comsan', 'eaywag1']

In [8]:
filtered_df = df[df['primary_label'].isin(interested_species)]

filtered_df.head()

primary_label secondary_labels                                type  \
895        barswa               []             ['call', 'flight call']   
896        barswa               []                            ['song']   
897        barswa               []                            ['song']   
898        barswa               []  ['call', 'female', 'male', 'song']   
899        barswa               []                            ['song']   

     latitude  longitude  scientific_name   common_name            author  \
895   46.4605     6.3914  Hirundo rustica  Barn Swallow         Bram Piot   
896   35.0307  -120.6205  Hirundo rustica  Barn Swallow  Thomas G. Graves   
897   45.3675   -73.8566  Hirundo rustica  Barn Swallow   Patrick Turgeon   
898   56.1559    47.4939  Hirundo rustica  Barn Swallow  Albert Lastukhin   
899   55.9937    -3.5605  Hirundo rustica  Barn Swallow       Mike Nelson   

                                               license  rating  \
895  Creative Commons Attribution-NonCommercial-Sha...     2.5   
896  Creative Commons Attribution-NonCommercial-Sha...     4.5   
897  Creative Commons Attribution-NonCommercial-Sha...     3.0   
898  Creative Commons Attribution-NonCommercial-Sha...     3.0   
899  Creative Commons Attribution-NonCommercial-Sha...     3.0   

                                   url             filename  
895  https://www.xeno-canto.org/113914  barswa/XC113914.ogg  
896  https://www.xeno-canto.org/129647  barswa/XC129647.ogg  
897  https://www.xeno-canto.org/132406  barswa/XC132406.ogg  
898  https://www.xeno-canto.org/133096  barswa/XC133096.ogg  
899  https://www.xeno-canto.org/133802  barswa/XC133802.ogg

In [9]:
filtered_df['primary_label'].value_counts()

barswa     500
comsan     500
eaywag1    500
Name: primary_label, dtype: int64

## 2. remove duplicates (same 'duration', 'location', 'type', 'primary_label', 'author')

### Step 1. Extract duration using librosa

In [10]:
# change the file path to your local path
path = '/content/drive/MyDrive/project/train_audio/'

In [11]:
sr = 16000

In [12]:
example = filtered_df['filename'].iloc[0]
example

'barswa/XC113914.ogg'

In [13]:
audio, _ = librosa.load(path + example, sr=sr)
Audio(audio, rate=sr)

In [14]:
def get_audio_duration(file_path, sr=sr):
  audio, _ = librosa.load(file_path, sr=sr)
  duration = librosa.get_duration(y=audio, sr=sr)
  return duration

In [15]:
filtered_df['duration'] = filtered_df['filename'].apply(lambda x: get_audio_duration(path + x))

<ipython-input-15-3ccdbaf6b56b>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  filtered_df['duration'] = filtered_df['filename'].apply(lambda x: get_audio_duration(path + x))


In [16]:
filtered_df['duration'].dtypes

dtype('float64')

In [17]:
filtered_df.head()

primary_label secondary_labels                                type  \
895        barswa               []             ['call', 'flight call']   
896        barswa               []                            ['song']   
897        barswa               []                            ['song']   
898        barswa               []  ['call', 'female', 'male', 'song']   
899        barswa               []                            ['song']   

     latitude  longitude  scientific_name   common_name            author  \
895   46.4605     6.3914  Hirundo rustica  Barn Swallow         Bram Piot   
896   35.0307  -120.6205  Hirundo rustica  Barn Swallow  Thomas G. Graves   
897   45.3675   -73.8566  Hirundo rustica  Barn Swallow   Patrick Turgeon   
898   56.1559    47.4939  Hirundo rustica  Barn Swallow  Albert Lastukhin   
899   55.9937    -3.5605  Hirundo rustica  Barn Swallow       Mike Nelson   

                                               license  rating  \
895  Creative Commons Attribution-NonCommercial-Sha...     2.5   
896  Creative Commons Attribution-NonCommercial-Sha...     4.5   
897  Creative Commons Attribution-NonCommercial-Sha...     3.0   
898  Creative Commons Attribution-NonCommercial-Sha...     3.0   
899  Creative Commons Attribution-NonCommercial-Sha...     3.0   

                                   url             filename    duration  
895  https://www.xeno-canto.org/113914  barswa/XC113914.ogg   57.077562  
896  https://www.xeno-canto.org/129647  barswa/XC129647.ogg  106.728000  
897  https://www.xeno-canto.org/132406  barswa/XC132406.ogg   10.788562  
898  https://www.xeno-canto.org/133096  barswa/XC133096.ogg   11.572250  
899  https://www.xeno-canto.org/133802  barswa/XC133802.ogg   15.490625

### Step 2. Find duplicates

same 'duration', 'location', 'type', 'primary_label', 'author'

In [19]:
duplicates = filtered_df.duplicated(subset=['duration', 'latitude', 'type', 'primary_label', 'author'], keep=False)
duplicated_rows = filtered_df[duplicates]

display(len(duplicated_rows))
display(duplicated_rows)

15

primary_label secondary_labels                               type  \
1203        barswa               []  ['call', 'song', 'various calls']   
1204        barswa               []  ['call', 'song', 'various calls']   
1289        barswa               []                  ['adult', 'song']   
1290        barswa               []                  ['adult', 'song']   
1316        barswa               []                           ['call']   
1318        barswa               []                           ['call']   
1389        barswa               []                               ['']   
1390        barswa               []                               ['']   
5287        comsan               []          ['nocturnal flight call']   
5288        comsan               []          ['nocturnal flight call']   
5289        comsan               []          ['nocturnal flight call']   
5322        comsan               []                           ['call']   
5323        comsan               []                           ['call']   
6067       eaywag1               []                    ['flight call']   
6069       eaywag1               []                    ['flight call']   

      latitude  longitude     scientific_name             common_name  \
1203   58.7542    23.8439     Hirundo rustica            Barn Swallow   
1204   58.7542    23.8439     Hirundo rustica            Barn Swallow   
1289   52.8858    23.8293     Hirundo rustica            Barn Swallow   
1290   52.8858    23.8293     Hirundo rustica            Barn Swallow   
1316   51.3672     5.8406     Hirundo rustica            Barn Swallow   
1318   51.3672     5.8406     Hirundo rustica            Barn Swallow   
1389   56.6346     9.7837     Hirundo rustica            Barn Swallow   
1390   56.6346     9.7837     Hirundo rustica            Barn Swallow   
5287   51.4309    -2.8518  Actitis hypoleucos        Common Sandpiper   
5288   51.4309    -2.8518  Actitis hypoleucos        Common Sandpiper   
5289   51.4309    -2.8518  Actitis hypoleucos        Common Sandpiper   
5322  -13.1010    31.7949  Actitis hypoleucos        Common Sandpiper   
5323  -13.1010    31.7949  Actitis hypoleucos        Common Sandpiper   
6067   44.1062     1.8827     Motacilla flava  Western Yellow Wagtail   
6069   44.1062     1.8827     Motacilla flava  Western Yellow Wagtail   

                author                                            license  \
1203   Stanislas Wroza  Creative Commons Attribution-NonCommercial-Sha...   
1204   Stanislas Wroza  Creative Commons Attribution-NonCommercial-Sha...   
1289  Ireneusz Oleksik  Creative Commons Attribution-NonCommercial-Sha...   
1290  Ireneusz Oleksik  Creative Commons Attribution-NonCommercial-Sha...   
1316        Ad Hilders  Creative Commons Attribution-NonCommercial-Sha...   
1318        Ad Hilders  Creative Commons Attribution-NonCommercial-Sha...   
1389        Ad Hilders  Creative Commons Attribution-NonCommercial-Sha...   
1390        Ad Hilders  Creative Commons Attribution-NonCommercial-Sha...   
5287     Paul Williams  Creative Commons Attribution-NonCommercial-Sha...   
5288     Paul Williams  Creative Commons Attribution-NonCommercial-Sha...   
5289     Paul Williams  Creative Commons Attribution-NonCommercial-Sha...   
5322     Meena Haribal  Creative Commons Attribution-NonCommercial-Sha...   
5323     Meena Haribal  Creative Commons Attribution-NonCommercial-Sha...   
6067    Cedric Mroczko  Creative Commons Attribution-NonCommercial-Sha...   
6069    Cedric Mroczko  Creative Commons Attribution-NonCommercial-Sha...   

      rating                                url              filename  \
1203     5.0  https://www.xeno-canto.org/575747   barswa/XC575747.ogg   
1204     0.0  https://www.xeno-canto.org/575749   barswa/XC575749.ogg   
1289     4.5  https://www.xeno-canto.org/664976   barswa/XC664976.ogg   
1290     4.5  https://www.xeno-canto.org/664977   barswa/XC664977.ogg   
1316     3.0       http://xeno-canto.org/671669   bar

In [20]:
dup1, _ = librosa.load(path + duplicated_rows['filename'].iloc[0], sr=sr)
Audio(dup1, rate=sr)

In [21]:
dup2, _ = librosa.load(path + duplicated_rows['filename'].iloc[1], sr=sr)
Audio(dup2, rate=sr)

### Step 3. Remove duplicates

In [22]:
display(len(filtered_df))

1500

In [23]:
filtered_df = filtered_df.drop_duplicates(subset=['duration', 'latitude', 'type', 'primary_label', 'author'], keep='first')

display(len(filtered_df))

1492

## 3. Split filtered_df to train and test

In [24]:
train_df, test_df = train_test_split(filtered_df, test_size=0.3, random_state=1234)

In [25]:
display(len(train_df))
display(train_df.head())

1044

primary_label secondary_labels  \
5295        comsan               []   
6169       eaywag1               []   
5388        comsan               []   
971         barswa               []   
1344        barswa               []   

                                                   type  latitude  longitude  \
5295           ['flight call', 'nocturnal flight call']   50.7542     4.5672   
6169                          ['call', 'sex uncertain']   69.3585    88.2378   
5388  ['life stage uncertain', 'nocturnal flight cal...   41.1698     0.9761   
971                       ['alarm call', 'flight call']       NaN        NaN   
1344                                           ['song']   53.9299    -2.9833   

         scientific_name             common_name               author  \
5295  Actitis hypoleucos        Common Sandpiper       Frederik Fluyt   
6169     Motacilla flava  Western Yellow Wagtail  Alexander Hellquist   
5388  Actitis hypoleucos        Common Sandpiper         Xavier Riera   
971      Hirundo rustica            Barn Swallow        Daniel Parker   
1344     Hirundo rustica            Barn Swallow          Chris Batty   

                                                license  rating  \
5295  Creative Commons Attribution-NonCommercial-Sha...     4.0   
6169  Creative Commons Attribution-NonCommercial-Sha...     3.0   
5388  Creative Commons Attribution-NonCommercial-Sha...     5.0   
971   Creative Commons Attribution-NonCommercial-Sha...     2.5   
1344  Creative Commons Attribution-NonCommercial-Sha...     2.5   

                                    url              filename   duration  
5295  https://www.xeno-canto.org/587730   comsan/XC587730.ogg   5.746937  
6169       http://xeno-canto.org/675944  eaywag1/XC675944.ogg   5.355000  
5388  https://www.xeno-canto.org/664012   comsan/XC664012.ogg  10.488000  
971   https://www.xeno-canto.org/268804   barswa/XC268804.ogg  76.538813  
1344       http://xeno-canto.org/690498   barswa/XC690498.ogg  83.095500

In [26]:
display(len(test_df))
display(test_df.head())

448

primary_label       secondary_labels  \
1364        barswa                     []   
5164        comsan                     []   
6211       eaywag1                     []   
5939       eaywag1  ['cohmar1', 'hoopoe']   
1356        barswa                     []   

                                          type  latitude  longitude  \
1364                                      ['']   53.2509     5.5980   
5164  ['flight call', 'nocturnal flight call']   48.8306     2.1999   
6211                                      ['']   43.3298     4.8364   
5939                   ['call', 'flight call']   37.1357    -7.6138   
1356                                      ['']   19.3551   -99.0467   

         scientific_name             common_name            author  \
1364     Hirundo rustica            Barn Swallow    Gosse Hoekstra   
5164  Actitis hypoleucos        Common Sandpiper   Stanislas Wroza   
6211     Motacilla flava  Western Yellow Wagtail   Stanislas Wroza   
5939     Motacilla flava  Western Yellow Wagtail  Nelson Conceição   
1356     Hirundo rustica            Barn Swallow  Manuel Grosselet   

                                                license  rating  \
1364  Creative Commons Attribution-NonCommercial-Sha...     4.0   
5164  Creative Commons Attribution-NonCommercial-Sha...     4.0   
6211  Creative Commons Attribution-NonCommercial-Sha...     4.0   
5939  Creative Commons Attribution-NonCommercial-Sha...     4.5   
1356  Creative Commons Attribution-NonCommercial-Sha...     5.0   

                                    url              filename    duration  
1364      https://xeno-canto.org/721711   barswa/XC721711.ogg   19.069375  
5164  https://www.xeno-canto.org/496602   comsan/XC496602.ogg   28.995938  
6211      https://xeno-canto.org/718445  eaywag1/XC718445.ogg    7.340438  
5939  https://www.xeno-canto.org/481360  eaywag1/XC481360.ogg  151.944000  
1356      https://xeno-canto.org/698512   barswa/XC698512.ogg   18.703688

# Save the train_df and test_df for future use

In [27]:
train_df.to_csv('/content/drive/MyDrive/project/train_df.csv', index=False)
test_df.to_csv('/content/drive/MyDrive/project/test_df.csv', index=False)